In [1]:
!pwd

/c/Users/ETHICSENSE/Desktop/aiffel/dataton/poc_lab/VoC_RM/code


In [2]:
import random
import pickle
import re

wordnet = {}
with open("../kwordnet/wordnet.pickle", "rb") as f:
	wordnet = pickle.load(f)


# 한글만 남기고 나머지는 삭제
def get_only_hangul(line):
	parseText= re.compile('/ ^[ㄱ-ㅎㅏ-ㅣ가-힣]*$/').sub('',line)

	return parseText



########################################################################
# Synonym replacement
# Replace n words in the sentence with synonyms from wordnet
########################################################################
def synonym_replacement(words, n):
	new_words = words.copy()
	random_word_list = list(set([word for word in words]))
	random.shuffle(random_word_list)
	num_replaced = 0
	for random_word in random_word_list:
		synonyms = get_synonyms(random_word)
		if len(synonyms) >= 1:
			synonym = random.choice(list(synonyms))
			new_words = [synonym if word == random_word else word for word in new_words]
			num_replaced += 1
		if num_replaced >= n:
			break

	if len(new_words) != 0:
		sentence = ' '.join(new_words)
		new_words = sentence.split(" ")

	else:
		new_words = ""

	return new_words


def get_synonyms(word):
	synomyms = []

	try:
		for syn in wordnet[word]:
			for s in syn:
				synomyms.append(s)
	except:
		pass

	return synomyms

########################################################################
# Random deletion
# Randomly delete words from the sentence with probability p
########################################################################
def random_deletion(words, p):
	if len(words) == 1:
		return words

	new_words = []
	for word in words:
		r = random.uniform(0, 1)
		if r > p:
			new_words.append(word)

	if len(new_words) == 0:
		rand_int = random.randint(0, len(words)-1)
		return [words[rand_int]]

	return new_words

########################################################################
# Random swap
# Randomly swap two words in the sentence n times
########################################################################
def random_swap(words, n):
	new_words = words.copy()
	for _ in range(n):
		new_words = swap_word(new_words)

	return new_words

def swap_word(new_words):
	random_idx_1 = random.randint(0, len(new_words)-1)
	random_idx_2 = random_idx_1
	counter = 0

	while random_idx_2 == random_idx_1:
		random_idx_2 = random.randint(0, len(new_words)-1)
		counter += 1
		if counter > 3:
			return new_words

	new_words[random_idx_1], new_words[random_idx_2] = new_words[random_idx_2], new_words[random_idx_1]
	return new_words

########################################################################
# Random insertion
# Randomly insert n words into the sentence
########################################################################
def random_insertion(words, n):
	new_words = words.copy()
	for _ in range(n):
		add_word(new_words)
	
	return new_words


def add_word(new_words):
	synonyms = []
	counter = 0
	while len(synonyms) < 1:
		if len(new_words) >= 1:
			random_word = new_words[random.randint(0, len(new_words)-1)]
			synonyms = get_synonyms(random_word)
			counter += 1
		else:
			random_word = ""

		if counter >= 10:
			return
		
	random_synonym = synonyms[0]
	random_idx = random.randint(0, len(new_words)-1)
	new_words.insert(random_idx, random_synonym)



def EDA(sentence, alpha_sr=0.1, alpha_ri=0.1, alpha_rs=0.1, p_rd=0.1, num_aug=9):
	sentence = get_only_hangul(sentence)
	words = sentence.split(' ')
	words = [word for word in words if word is not ""]
	num_words = len(words)

	augmented_sentences = []
	num_new_per_technique = int(num_aug/4) + 1

	n_sr = max(1, int(alpha_sr*num_words))
	n_ri = max(1, int(alpha_ri*num_words))
	n_rs = max(1, int(alpha_rs*num_words))

	# sr
	for _ in range(num_new_per_technique):
		a_words = synonym_replacement(words, n_sr)
		augmented_sentences.append(' '.join(a_words))

	# ri
	for _ in range(num_new_per_technique):
		a_words = random_insertion(words, n_ri)
		augmented_sentences.append(' '.join(a_words))

	# rs
	for _ in range(num_new_per_technique):
		a_words = random_swap(words, n_rs)
		augmented_sentences.append(" ".join(a_words))

	# rd
	for _ in range(num_new_per_technique):
		a_words = random_deletion(words, p_rd)
		augmented_sentences.append(" ".join(a_words))

	augmented_sentences = [get_only_hangul(sentence) for sentence in augmented_sentences]
	random.shuffle(augmented_sentences)

	if num_aug >= 1:
		augmented_sentences = augmented_sentences[:num_aug]
	else:
		keep_prob = num_aug / len(augmented_sentences)
		augmented_sentences = [s for s in augmented_sentences if random.uniform(0, 1) < keep_prob]

	augmented_sentences.append(sentence)

	return augmented_sentences

<>:138: SyntaxWarning: "is not" with a literal. Did you mean "!="?
<>:138: SyntaxWarning: "is not" with a literal. Did you mean "!="?
<ipython-input-2-ca7d3b6de97a>:138: SyntaxWarning: "is not" with a literal. Did you mean "!="?
  words = [word for word in words if word is not ""]


In [3]:
import pandas as pd

data_path = '../datasets/dktc/data/insert_koen/train.csv'
df = pd.read_csv(data_path)

df.head(10)

idx  label     class                                       conversation
0    0      1        협박  지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 ...
1    1      1        협박  길동경찰서입니다.\n9시 40분 마트에 폭발물을 설치할거다.\n네?\n똑바로 들어 ...
2    2      1    기타 괴롭힘  너 되게 귀여운거 알지? 나보다 작은 남자는 첨봤어.\n그만해. 니들 놀리는거 재미...
3    3      1        갈취  어이 거기\n예??\n너 말이야 너. 이리 오라고\n무슨 일.\n너 옷 좋아보인다?...
4    4      1        갈취  저기요 혹시 날이 너무 뜨겁잖아요? 저희 회사에서 이 선크림 파는데 한 번 손등에 ...
5    5      1  직장 내 괴롭힘  나 이틀뒤에 가나다 음식점 예약좀 해줘. 저녁7시로.\n가나다 음식점이요.?\n응....
6    6      1    기타 괴롭힘  35번 손님 아이스커피 두잔나왔습니다\n아이스커피? \n네 맛있게드세요\n저기요 아...
7    7      1    기타 괴롭힘  경비아저씨 내차에 경고장 붙였어요?\n내가 여기 몇년째 사는데 아직도 내차인줄 모르...
8    8      1    기타 괴롭힘  이거 할인 된다면서요\n 확인해보겠습니다\n 아까 저 시람은 할인 해주던데\n 네 ...
9    9      1        갈취  자네 세금계산서 보내준 거 메일이랑 수치가 다르던데?\n그게.\n얼마나 해먹었어? ...

In [4]:
df.tail(10)

idx  label class                                       conversation
7889  7218      0    일반  지금 레슨을 일주일에 몇 회 받고 계시는지요?\n일주일에 2회 받고는 있는데, 점점...
7890  7219      0    일반  요즘 날이 더워서 다이어트 식단을 유지하기 힘들어요.\n제가 이전에 말씀드렸던 식단...
7891  7220      0    일반  유산소 운동과 근력 운동의 차이가 도대체 뭔가요?\n여성분들도 근력 운동을 하셔야 ...
7892  7221      0    일반  이제부터 매일 운동 시간을 늘려보려고 하는데요.\n지금까지는 하루에 어느 정도 운동...
7893  7222      0    일반  이제는 필라테스나 요가도 함께 해보고 싶은데 괜찮나요?\n어느 정도 근육통을 회복하...
7894  7223      0    일반  필라테스 호흡에서는 조금 더 코어 근육에 집중합니다.\n말로 하는 설명만 들어서는 ...
7895  7224      0    일반  아주 어린 아이들도 짐볼로 운동을 하기 때문에 괜찮습니다.\n발목을 접질릴까봐 무서...
7896  7225      0    일반  의사가 가벼운 운동은 괜찮다고 해서 요가를 했어요.\n기본적인 근력 운동을 계속하셨...
7897  7226      0    일반  집안에 일이 생겨서 거기에 집중해야 할 것 같아요.\n그럼 회원권은 잠시 정지 시켜...
7898  7227      0    일반  러닝머신이나 자전거 같은 운동을 할 때 소리가 나요.\n유산소 운동을 할 때 장의 ...

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7899 entries, 0 to 7898
Data columns (total 4 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   idx           7899 non-null   int64 
 1   label         7899 non-null   int64 
 2   class         7899 non-null   object
 3   conversation  7899 non-null   object
dtypes: int64(2), object(2)
memory usage: 247.0+ KB


In [6]:
df['conversation'][0]

'지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 거면 혼자 죽지 우리까지 사건에 휘말리게 해? 진짜 죽여버리고 싶게.\n 정말 잘못했습니다.\n 너가 선택해. 너가 죽을래 네 가족을 죽여줄까.\n 죄송합니다. 정말 잘못했습니다.\n 너에게는 선택권이 없어. 선택 못한다면 너와 네 가족까지 모조리 죽여버릴거야.\n 선택 못하겠습니다. 한번만 도와주세요.\n 그냥 다 죽여버려야겠군. 이의 없지?\n 제발 도와주세요.'

In [7]:
test_sentence = df['conversation'][0]

test_sentence

'지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 거면 혼자 죽지 우리까지 사건에 휘말리게 해? 진짜 죽여버리고 싶게.\n 정말 잘못했습니다.\n 너가 선택해. 너가 죽을래 네 가족을 죽여줄까.\n 죄송합니다. 정말 잘못했습니다.\n 너에게는 선택권이 없어. 선택 못한다면 너와 네 가족까지 모조리 죽여버릴거야.\n 선택 못하겠습니다. 한번만 도와주세요.\n 그냥 다 죽여버려야겠군. 이의 없지?\n 제발 도와주세요.'

In [8]:
temp = EDA(test_sentence)

In [9]:
get_only_hangul(test_sentence)

'지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 거면 혼자 죽지 우리까지 사건에 휘말리게 해? 진짜 죽여버리고 싶게.\n 정말 잘못했습니다.\n 너가 선택해. 너가 죽을래 네 가족을 죽여줄까.\n 죄송합니다. 정말 잘못했습니다.\n 너에게는 선택권이 없어. 선택 못한다면 너와 네 가족까지 모조리 죽여버릴거야.\n 선택 못하겠습니다. 한번만 도와주세요.\n 그냥 다 죽여버려야겠군. 이의 없지?\n 제발 도와주세요.'

In [10]:
len(df)

7899

In [11]:
df.head()

idx  label   class                                       conversation
0    0      1      협박  지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 ...
1    1      1      협박  길동경찰서입니다.\n9시 40분 마트에 폭발물을 설치할거다.\n네?\n똑바로 들어 ...
2    2      1  기타 괴롭힘  너 되게 귀여운거 알지? 나보다 작은 남자는 첨봤어.\n그만해. 니들 놀리는거 재미...
3    3      1      갈취  어이 거기\n예??\n너 말이야 너. 이리 오라고\n무슨 일.\n너 옷 좋아보인다?...
4    4      1      갈취  저기요 혹시 날이 너무 뜨겁잖아요? 저희 회사에서 이 선크림 파는데 한 번 손등에 ...

In [12]:
df[df['class']=='협박'].iloc[3, 3]

'너가 민수라는 남자 제자니?\n네 맞는데요 왜 그러시죠? 혹시 저희 선생님께 무슨 일 생겼나요?\n무슨 일은 그냥 선생님 콩팥 하나 정도 가져가려고\n네.? 장난치시지 마세요. 장난이 너무 심하신 거 아니신가요?\n아 어린애라 그런지 상황 판단 못하네 사진 보내 줄 테니 봐봐 장난인지 아닌지\n어.? 왜 그러시는 건가요 신고 할 거예요 당장 신고 할 거예요.\n신고해보던지 어딘지는 알고 신고하게?\n저한테 원하시는 거 있으시면 최대한 할게요 선생님 해치지 말아주세요\n그럼 내가 말하는 거 가져다 주기만 해 그러면 그냥 깔끔하게 끝날 일이야\n그렇게 하도록 할게요 바로 할게요'

In [13]:
df.iloc[200, 3]

'야 민식아 너 몇달전에 빌린 내 돈 좀 다시 돌려줘야겠다. 내가 급해서 말이야\n뭐 갑자기?? 나도 지금 쪼들린단 말이야. 세 달 뒤에 갚으면 안될까?\n뭐? 내가 지금 다섯달 기다렸으면 많이 기다린 거 아니야? 서울 살면서 뭐가 쪼들려? 내가 빌려준 건 생각 안 하냐?\n야 뭔 말을 그렇게 하냐 내가 그냥 가져 갔냐? 훔쳤어? 내가 다시 돌려준다고 했잖아\n야 이게 미쳤냐? 니가 뭔데 언성을 높혀 뭐가 잘났다고!\n참나 이거 본성 나오네. 나도 니 말고 빌릴 사람 많아. 그냥 빌린것도 아니고 이자 4씩 쳐준다고 했잖아.\n됐고 두시간안에 빌린 돈 계좌로 입금안 하면 니 엄마 아빠 할아버지 동생까지 싹 다 농약 먹여서 죽여버릴거니까 생각 잘 해.\n뭐? 이게 미쳤냐? 그러고도 너는 무사 할 거 같냐?\n그럼 그냥 가족들이랑 영영 못 만나고 헤어지던가 \n알았어. 조금만 더 시간을 줘 가족들은 건들지 말아줘.'

In [14]:
df.columns

Index(['idx', 'label', 'class', 'conversation'], dtype='object')

In [15]:
df.iloc[0,2]

'협박'

In [16]:
temp

['지금 너 스스로를 애원하는 것인가?\n 아닙니다. 거면 혼자 죽지 사건에 휘말리게 해? 진짜 죽여버리고 싶게.\n 정말 잘못했습니다.\n 선택해. 너가 죽을래 가족을 죽여줄까.\n 죄송합니다. 잘못했습니다.\n 선택권이 선택 못한다면 너와 네 가족까지 모조리 죽여버릴거야.\n 선택 못하겠습니다. 한번만 그냥 다 죽여버려야겠군. 이의 없지?\n 제발 도와주세요.',
 '지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 거면 혼자 죽지 우리까지 사건에 휘말리게 해? 짜 죽여버리고 싶게.\n 정말 잘못했습니다.\n 너가 선택해. 너가 죽을래 네 가족을 죽여줄까.\n 죄송합니다. 정말 잘못했습니다.\n 너에게는 선택권이 없어. 선택 못한다면 너와 네 가족까지 모조리 죽여버릴거야.\n 선택 못하겠습니다. 한번만 도와주세요.\n 그냥 다 죽여버려야겠군. 이의 없지?\n 제발 도와주세요.',
 '지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 선택권이 거면 못한다면 죽지 우리까지 사건에 휘말리게 해? 진짜 죽여버리고 선택해. 정말 잘못했습니다.\n 너가 싶게.\n 너가 죽을래 네 가족을 죽여줄까.\n 죄송합니다. 정말 잘못했습니다.\n 너에게는 죽을 없어. 선택 혼자 너와 네 도와주세요.\n 모조리 죽여버릴거야.\n 선택 못하겠습니다. 한번만 죽여버려야겠군. 그냥 다 가족까지 이의 없지?\n 제발 도와주세요.',
 '지금 네 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 혼자 거면 죽지 우리까지 사건에 휘말리게 해? 진짜 죽여버리고 선택해. 정말 잘못했습니다.\n 정말 싶게.\n 너가 죽을래 네 가족을 죽여줄까.\n 죄송합니다. 선택권이 잘못했습니다.\n 너에게는 너가 없어. 선택 못한다면 너와 너 가족까지 모조리 죽여버릴거야.\n 선택 못하겠습니다. 한번만 도와주세요.\n 그냥 다 죽여버려야겠군. 이의 없지?\n 제발 도와주세요.',
 '지금 너 스스로를 죽여달라고 애원하는 것인가

In [17]:
len(temp)

10

In [18]:
df.append({'class' : df.iloc[0,2], 'conversation' : temp[0]}, ignore_index=True)

idx  label   class                                       conversation
0        0.0    1.0      협박  지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 ...
1        1.0    1.0      협박  길동경찰서입니다.\n9시 40분 마트에 폭발물을 설치할거다.\n네?\n똑바로 들어 ...
2        2.0    1.0  기타 괴롭힘  너 되게 귀여운거 알지? 나보다 작은 남자는 첨봤어.\n그만해. 니들 놀리는거 재미...
3        3.0    1.0      갈취  어이 거기\n예??\n너 말이야 너. 이리 오라고\n무슨 일.\n너 옷 좋아보인다?...
4        4.0    1.0      갈취  저기요 혹시 날이 너무 뜨겁잖아요? 저희 회사에서 이 선크림 파는데 한 번 손등에 ...
...      ...    ...     ...                                                ...
7895  7224.0    0.0      일반  아주 어린 아이들도 짐볼로 운동을 하기 때문에 괜찮습니다.\n발목을 접질릴까봐 무서...
7896  7225.0    0.0      일반  의사가 가벼운 운동은 괜찮다고 해서 요가를 했어요.\n기본적인 근력 운동을 계속하셨...
7897  7226.0    0.0      일반  집안에 일이 생겨서 거기에 집중해야 할 것 같아요.\n그럼 회원권은 잠시 정지 시켜...
7898  7227.0    0.0      일반  러닝머신이나 자전거 같은 운동을 할 때 소리가 나요.\n유산소 운동을 할 때 장의 ...
7899     NaN    NaN      협박  지금 너 스스로를 애원하는 것인가?\n 아닙니다. 거면 혼자 죽지 사건에 휘말리게 ...

[7900 rows x 4 columns]

In [19]:
df.tail()

idx  label class                                       conversation
7894  7223      0    일반  필라테스 호흡에서는 조금 더 코어 근육에 집중합니다.\n말로 하는 설명만 들어서는 ...
7895  7224      0    일반  아주 어린 아이들도 짐볼로 운동을 하기 때문에 괜찮습니다.\n발목을 접질릴까봐 무서...
7896  7225      0    일반  의사가 가벼운 운동은 괜찮다고 해서 요가를 했어요.\n기본적인 근력 운동을 계속하셨...
7897  7226      0    일반  집안에 일이 생겨서 거기에 집중해야 할 것 같아요.\n그럼 회원권은 잠시 정지 시켜...
7898  7227      0    일반  러닝머신이나 자전거 같은 운동을 할 때 소리가 나요.\n유산소 운동을 할 때 장의 ...

In [20]:
cnt = 1

for i in range(len(df)):
    tmp = df.iloc[i, 3]
    tmp = EDA(tmp)
    for sentence in tmp :
        df = df.append({'class' : df.iloc[i, 2], 'conversation' : sentence}, ignore_index=True)
        print(cnt, '번째 증강 데이터 삽입 성공')
        cnt += 1

1 번째 증강 데이터 삽입 성공
2 번째 증강 데이터 삽입 성공
3 번째 증강 데이터 삽입 성공
4 번째 증강 데이터 삽입 성공
5 번째 증강 데이터 삽입 성공
6 번째 증강 데이터 삽입 성공
7 번째 증강 데이터 삽입 성공
8 번째 증강 데이터 삽입 성공
9 번째 증강 데이터 삽입 성공
10 번째 증강 데이터 삽입 성공
11 번째 증강 데이터 삽입 성공
12 번째 증강 데이터 삽입 성공
13 번째 증강 데이터 삽입 성공
14 번째 증강 데이터 삽입 성공
15 번째 증강 데이터 삽입 성공
16 번째 증강 데이터 삽입 성공
17 번째 증강 데이터 삽입 성공
18 번째 증강 데이터 삽입 성공
19 번째 증강 데이터 삽입 성공
20 번째 증강 데이터 삽입 성공
21 번째 증강 데이터 삽입 성공
22 번째 증강 데이터 삽입 성공
23 번째 증강 데이터 삽입 성공
24 번째 증강 데이터 삽입 성공
25 번째 증강 데이터 삽입 성공
26 번째 증강 데이터 삽입 성공
27 번째 증강 데이터 삽입 성공
28 번째 증강 데이터 삽입 성공
29 번째 증강 데이터 삽입 성공
30 번째 증강 데이터 삽입 성공
31 번째 증강 데이터 삽입 성공
32 번째 증강 데이터 삽입 성공
33 번째 증강 데이터 삽입 성공
34 번째 증강 데이터 삽입 성공
35 번째 증강 데이터 삽입 성공
36 번째 증강 데이터 삽입 성공
37 번째 증강 데이터 삽입 성공
38 번째 증강 데이터 삽입 성공
39 번째 증강 데이터 삽입 성공
40 번째 증강 데이터 삽입 성공
41 번째 증강 데이터 삽입 성공
42 번째 증강 데이터 삽입 성공
43 번째 증강 데이터 삽입 성공
44 번째 증강 데이터 삽입 성공
45 번째 증강 데이터 삽입 성공
46 번째 증강 데이터 삽입 성공
47 번째 증강 데이터 삽입 성공
48 번째 증강 데이터 삽입 성공
49 번째 증강 데이터 삽입 성공
50 번째 증강 데이터 삽입 성공
51 번째 증강 데이터 삽입 성공
52 번째 증강 데이터 삽입 성공
53 번째 증강 데이터 삽입 성공
54

451 번째 증강 데이터 삽입 성공
452 번째 증강 데이터 삽입 성공
453 번째 증강 데이터 삽입 성공
454 번째 증강 데이터 삽입 성공
455 번째 증강 데이터 삽입 성공
456 번째 증강 데이터 삽입 성공
457 번째 증강 데이터 삽입 성공
458 번째 증강 데이터 삽입 성공
459 번째 증강 데이터 삽입 성공
460 번째 증강 데이터 삽입 성공
461 번째 증강 데이터 삽입 성공
462 번째 증강 데이터 삽입 성공
463 번째 증강 데이터 삽입 성공
464 번째 증강 데이터 삽입 성공
465 번째 증강 데이터 삽입 성공
466 번째 증강 데이터 삽입 성공
467 번째 증강 데이터 삽입 성공
468 번째 증강 데이터 삽입 성공
469 번째 증강 데이터 삽입 성공
470 번째 증강 데이터 삽입 성공
471 번째 증강 데이터 삽입 성공
472 번째 증강 데이터 삽입 성공
473 번째 증강 데이터 삽입 성공
474 번째 증강 데이터 삽입 성공
475 번째 증강 데이터 삽입 성공
476 번째 증강 데이터 삽입 성공
477 번째 증강 데이터 삽입 성공
478 번째 증강 데이터 삽입 성공
479 번째 증강 데이터 삽입 성공
480 번째 증강 데이터 삽입 성공
481 번째 증강 데이터 삽입 성공
482 번째 증강 데이터 삽입 성공
483 번째 증강 데이터 삽입 성공
484 번째 증강 데이터 삽입 성공
485 번째 증강 데이터 삽입 성공
486 번째 증강 데이터 삽입 성공
487 번째 증강 데이터 삽입 성공
488 번째 증강 데이터 삽입 성공
489 번째 증강 데이터 삽입 성공
490 번째 증강 데이터 삽입 성공
491 번째 증강 데이터 삽입 성공
492 번째 증강 데이터 삽입 성공
493 번째 증강 데이터 삽입 성공
494 번째 증강 데이터 삽입 성공
495 번째 증강 데이터 삽입 성공
496 번째 증강 데이터 삽입 성공
497 번째 증강 데이터 삽입 성공
498 번째 증강 데이터 삽입 성공
499 번째 증강 데이터 삽입 성공
500 번째 증강 데이터 삽입 성공


898 번째 증강 데이터 삽입 성공
899 번째 증강 데이터 삽입 성공
900 번째 증강 데이터 삽입 성공
901 번째 증강 데이터 삽입 성공
902 번째 증강 데이터 삽입 성공
903 번째 증강 데이터 삽입 성공
904 번째 증강 데이터 삽입 성공
905 번째 증강 데이터 삽입 성공
906 번째 증강 데이터 삽입 성공
907 번째 증강 데이터 삽입 성공
908 번째 증강 데이터 삽입 성공
909 번째 증강 데이터 삽입 성공
910 번째 증강 데이터 삽입 성공
911 번째 증강 데이터 삽입 성공
912 번째 증강 데이터 삽입 성공
913 번째 증강 데이터 삽입 성공
914 번째 증강 데이터 삽입 성공
915 번째 증강 데이터 삽입 성공
916 번째 증강 데이터 삽입 성공
917 번째 증강 데이터 삽입 성공
918 번째 증강 데이터 삽입 성공
919 번째 증강 데이터 삽입 성공
920 번째 증강 데이터 삽입 성공
921 번째 증강 데이터 삽입 성공
922 번째 증강 데이터 삽입 성공
923 번째 증강 데이터 삽입 성공
924 번째 증강 데이터 삽입 성공
925 번째 증강 데이터 삽입 성공
926 번째 증강 데이터 삽입 성공
927 번째 증강 데이터 삽입 성공
928 번째 증강 데이터 삽입 성공
929 번째 증강 데이터 삽입 성공
930 번째 증강 데이터 삽입 성공
931 번째 증강 데이터 삽입 성공
932 번째 증강 데이터 삽입 성공
933 번째 증강 데이터 삽입 성공
934 번째 증강 데이터 삽입 성공
935 번째 증강 데이터 삽입 성공
936 번째 증강 데이터 삽입 성공
937 번째 증강 데이터 삽입 성공
938 번째 증강 데이터 삽입 성공
939 번째 증강 데이터 삽입 성공
940 번째 증강 데이터 삽입 성공
941 번째 증강 데이터 삽입 성공
942 번째 증강 데이터 삽입 성공
943 번째 증강 데이터 삽입 성공
944 번째 증강 데이터 삽입 성공
945 번째 증강 데이터 삽입 성공
946 번째 증강 데이터 삽입 성공
947 번째 증강 데이터 삽입 성공


1351 번째 증강 데이터 삽입 성공
1352 번째 증강 데이터 삽입 성공
1353 번째 증강 데이터 삽입 성공
1354 번째 증강 데이터 삽입 성공
1355 번째 증강 데이터 삽입 성공
1356 번째 증강 데이터 삽입 성공
1357 번째 증강 데이터 삽입 성공
1358 번째 증강 데이터 삽입 성공
1359 번째 증강 데이터 삽입 성공
1360 번째 증강 데이터 삽입 성공
1361 번째 증강 데이터 삽입 성공
1362 번째 증강 데이터 삽입 성공
1363 번째 증강 데이터 삽입 성공
1364 번째 증강 데이터 삽입 성공
1365 번째 증강 데이터 삽입 성공
1366 번째 증강 데이터 삽입 성공
1367 번째 증강 데이터 삽입 성공
1368 번째 증강 데이터 삽입 성공
1369 번째 증강 데이터 삽입 성공
1370 번째 증강 데이터 삽입 성공
1371 번째 증강 데이터 삽입 성공
1372 번째 증강 데이터 삽입 성공
1373 번째 증강 데이터 삽입 성공
1374 번째 증강 데이터 삽입 성공
1375 번째 증강 데이터 삽입 성공
1376 번째 증강 데이터 삽입 성공
1377 번째 증강 데이터 삽입 성공
1378 번째 증강 데이터 삽입 성공
1379 번째 증강 데이터 삽입 성공
1380 번째 증강 데이터 삽입 성공
1381 번째 증강 데이터 삽입 성공
1382 번째 증강 데이터 삽입 성공
1383 번째 증강 데이터 삽입 성공
1384 번째 증강 데이터 삽입 성공
1385 번째 증강 데이터 삽입 성공
1386 번째 증강 데이터 삽입 성공
1387 번째 증강 데이터 삽입 성공
1388 번째 증강 데이터 삽입 성공
1389 번째 증강 데이터 삽입 성공
1390 번째 증강 데이터 삽입 성공
1391 번째 증강 데이터 삽입 성공
1392 번째 증강 데이터 삽입 성공
1393 번째 증강 데이터 삽입 성공
1394 번째 증강 데이터 삽입 성공
1395 번째 증강 데이터 삽입 성공
1396 번째 증강 데이터 삽입 성공
1397 번째 증강 데이터 삽입 성공
1398 번째 증강 데이

1792 번째 증강 데이터 삽입 성공
1793 번째 증강 데이터 삽입 성공
1794 번째 증강 데이터 삽입 성공
1795 번째 증강 데이터 삽입 성공
1796 번째 증강 데이터 삽입 성공
1797 번째 증강 데이터 삽입 성공
1798 번째 증강 데이터 삽입 성공
1799 번째 증강 데이터 삽입 성공
1800 번째 증강 데이터 삽입 성공
1801 번째 증강 데이터 삽입 성공
1802 번째 증강 데이터 삽입 성공
1803 번째 증강 데이터 삽입 성공
1804 번째 증강 데이터 삽입 성공
1805 번째 증강 데이터 삽입 성공
1806 번째 증강 데이터 삽입 성공
1807 번째 증강 데이터 삽입 성공
1808 번째 증강 데이터 삽입 성공
1809 번째 증강 데이터 삽입 성공
1810 번째 증강 데이터 삽입 성공
1811 번째 증강 데이터 삽입 성공
1812 번째 증강 데이터 삽입 성공
1813 번째 증강 데이터 삽입 성공
1814 번째 증강 데이터 삽입 성공
1815 번째 증강 데이터 삽입 성공
1816 번째 증강 데이터 삽입 성공
1817 번째 증강 데이터 삽입 성공
1818 번째 증강 데이터 삽입 성공
1819 번째 증강 데이터 삽입 성공
1820 번째 증강 데이터 삽입 성공
1821 번째 증강 데이터 삽입 성공
1822 번째 증강 데이터 삽입 성공
1823 번째 증강 데이터 삽입 성공
1824 번째 증강 데이터 삽입 성공
1825 번째 증강 데이터 삽입 성공
1826 번째 증강 데이터 삽입 성공
1827 번째 증강 데이터 삽입 성공
1828 번째 증강 데이터 삽입 성공
1829 번째 증강 데이터 삽입 성공
1830 번째 증강 데이터 삽입 성공
1831 번째 증강 데이터 삽입 성공
1832 번째 증강 데이터 삽입 성공
1833 번째 증강 데이터 삽입 성공
1834 번째 증강 데이터 삽입 성공
1835 번째 증강 데이터 삽입 성공
1836 번째 증강 데이터 삽입 성공
1837 번째 증강 데이터 삽입 성공
1838 번째 증강 데이터 삽입 성공
1839 번째 증강 데이

...

77107 번째 증강 데이터 삽입 성공
77108 번째 증강 데이터 삽입 성공
77109 번째 증강 데이터 삽입 성공
77110 번째 증강 데이터 삽입 성공
77111 번째 증강 데이터 삽입 성공
77112 번째 증강 데이터 삽입 성공
77113 번째 증강 데이터 삽입 성공
77114 번째 증강 데이터 삽입 성공
77115 번째 증강 데이터 삽입 성공
77116 번째 증강 데이터 삽입 성공
77117 번째 증강 데이터 삽입 성공
77118 번째 증강 데이터 삽입 성공
77119 번째 증강 데이터 삽입 성공
77120 번째 증강 데이터 삽입 성공
77121 번째 증강 데이터 삽입 성공
77122 번째 증강 데이터 삽입 성공
77123 번째 증강 데이터 삽입 성공
77124 번째 증강 데이터 삽입 성공
77125 번째 증강 데이터 삽입 성공
77126 번째 증강 데이터 삽입 성공
77127 번째 증강 데이터 삽입 성공
77128 번째 증강 데이터 삽입 성공
77129 번째 증강 데이터 삽입 성공
77130 번째 증강 데이터 삽입 성공
77131 번째 증강 데이터 삽입 성공
77132 번째 증강 데이터 삽입 성공
77133 번째 증강 데이터 삽입 성공
77134 번째 증강 데이터 삽입 성공
77135 번째 증강 데이터 삽입 성공
77136 번째 증강 데이터 삽입 성공
77137 번째 증강 데이터 삽입 성공
77138 번째 증강 데이터 삽입 성공
77139 번째 증강 데이터 삽입 성공
77140 번째 증강 데이터 삽입 성공
77141 번째 증강 데이터 삽입 성공
77142 번째 증강 데이터 삽입 성공
77143 번째 증강 데이터 삽입 성공
77144 번째 증강 데이터 삽입 성공
77145 번째 증강 데이터 삽입 성공
77146 번째 증강 데이터 삽입 성공
77147 번째 증강 데이터 삽입 성공
77148 번째 증강 데이터 삽입 성공
77149 번째 증강 데이터 삽입 성공
77150 번째 증강 데이터 삽입 성공
77151 번째 증강 데이터 삽입 성공
77152 번째 증

77483 번째 증강 데이터 삽입 성공
77484 번째 증강 데이터 삽입 성공
77485 번째 증강 데이터 삽입 성공
77486 번째 증강 데이터 삽입 성공
77487 번째 증강 데이터 삽입 성공
77488 번째 증강 데이터 삽입 성공
77489 번째 증강 데이터 삽입 성공
77490 번째 증강 데이터 삽입 성공
77491 번째 증강 데이터 삽입 성공
77492 번째 증강 데이터 삽입 성공
77493 번째 증강 데이터 삽입 성공
77494 번째 증강 데이터 삽입 성공
77495 번째 증강 데이터 삽입 성공
77496 번째 증강 데이터 삽입 성공
77497 번째 증강 데이터 삽입 성공
77498 번째 증강 데이터 삽입 성공
77499 번째 증강 데이터 삽입 성공
77500 번째 증강 데이터 삽입 성공
77501 번째 증강 데이터 삽입 성공
77502 번째 증강 데이터 삽입 성공
77503 번째 증강 데이터 삽입 성공
77504 번째 증강 데이터 삽입 성공
77505 번째 증강 데이터 삽입 성공
77506 번째 증강 데이터 삽입 성공
77507 번째 증강 데이터 삽입 성공
77508 번째 증강 데이터 삽입 성공
77509 번째 증강 데이터 삽입 성공
77510 번째 증강 데이터 삽입 성공
77511 번째 증강 데이터 삽입 성공
77512 번째 증강 데이터 삽입 성공
77513 번째 증강 데이터 삽입 성공
77514 번째 증강 데이터 삽입 성공
77515 번째 증강 데이터 삽입 성공
77516 번째 증강 데이터 삽입 성공
77517 번째 증강 데이터 삽입 성공
77518 번째 증강 데이터 삽입 성공
77519 번째 증강 데이터 삽입 성공
77520 번째 증강 데이터 삽입 성공
77521 번째 증강 데이터 삽입 성공
77522 번째 증강 데이터 삽입 성공
77523 번째 증강 데이터 삽입 성공
77524 번째 증강 데이터 삽입 성공
77525 번째 증강 데이터 삽입 성공
77526 번째 증강 데이터 삽입 성공
77527 번째 증강 데이터 삽입 성공
77528 번째 증

77877 번째 증강 데이터 삽입 성공
77878 번째 증강 데이터 삽입 성공
77879 번째 증강 데이터 삽입 성공
77880 번째 증강 데이터 삽입 성공
77881 번째 증강 데이터 삽입 성공
77882 번째 증강 데이터 삽입 성공
77883 번째 증강 데이터 삽입 성공
77884 번째 증강 데이터 삽입 성공
77885 번째 증강 데이터 삽입 성공
77886 번째 증강 데이터 삽입 성공
77887 번째 증강 데이터 삽입 성공
77888 번째 증강 데이터 삽입 성공
77889 번째 증강 데이터 삽입 성공
77890 번째 증강 데이터 삽입 성공
77891 번째 증강 데이터 삽입 성공
77892 번째 증강 데이터 삽입 성공
77893 번째 증강 데이터 삽입 성공
77894 번째 증강 데이터 삽입 성공
77895 번째 증강 데이터 삽입 성공
77896 번째 증강 데이터 삽입 성공
77897 번째 증강 데이터 삽입 성공
77898 번째 증강 데이터 삽입 성공
77899 번째 증강 데이터 삽입 성공
77900 번째 증강 데이터 삽입 성공
77901 번째 증강 데이터 삽입 성공
77902 번째 증강 데이터 삽입 성공
77903 번째 증강 데이터 삽입 성공
77904 번째 증강 데이터 삽입 성공
77905 번째 증강 데이터 삽입 성공
77906 번째 증강 데이터 삽입 성공
77907 번째 증강 데이터 삽입 성공
77908 번째 증강 데이터 삽입 성공
77909 번째 증강 데이터 삽입 성공
77910 번째 증강 데이터 삽입 성공
77911 번째 증강 데이터 삽입 성공
77912 번째 증강 데이터 삽입 성공
77913 번째 증강 데이터 삽입 성공
77914 번째 증강 데이터 삽입 성공
77915 번째 증강 데이터 삽입 성공
77916 번째 증강 데이터 삽입 성공
77917 번째 증강 데이터 삽입 성공
77918 번째 증강 데이터 삽입 성공
77919 번째 증강 데이터 삽입 성공
77920 번째 증강 데이터 삽입 성공
77921 번째 증강 데이터 삽입 성공
77922 번째 증

78254 번째 증강 데이터 삽입 성공
78255 번째 증강 데이터 삽입 성공
78256 번째 증강 데이터 삽입 성공
78257 번째 증강 데이터 삽입 성공
78258 번째 증강 데이터 삽입 성공
78259 번째 증강 데이터 삽입 성공
78260 번째 증강 데이터 삽입 성공
78261 번째 증강 데이터 삽입 성공
78262 번째 증강 데이터 삽입 성공
78263 번째 증강 데이터 삽입 성공
78264 번째 증강 데이터 삽입 성공
78265 번째 증강 데이터 삽입 성공
78266 번째 증강 데이터 삽입 성공
78267 번째 증강 데이터 삽입 성공
78268 번째 증강 데이터 삽입 성공
78269 번째 증강 데이터 삽입 성공
78270 번째 증강 데이터 삽입 성공
78271 번째 증강 데이터 삽입 성공
78272 번째 증강 데이터 삽입 성공
78273 번째 증강 데이터 삽입 성공
78274 번째 증강 데이터 삽입 성공
78275 번째 증강 데이터 삽입 성공
78276 번째 증강 데이터 삽입 성공
78277 번째 증강 데이터 삽입 성공
78278 번째 증강 데이터 삽입 성공
78279 번째 증강 데이터 삽입 성공
78280 번째 증강 데이터 삽입 성공
78281 번째 증강 데이터 삽입 성공
78282 번째 증강 데이터 삽입 성공
78283 번째 증강 데이터 삽입 성공
78284 번째 증강 데이터 삽입 성공
78285 번째 증강 데이터 삽입 성공
78286 번째 증강 데이터 삽입 성공
78287 번째 증강 데이터 삽입 성공
78288 번째 증강 데이터 삽입 성공
78289 번째 증강 데이터 삽입 성공
78290 번째 증강 데이터 삽입 성공
78291 번째 증강 데이터 삽입 성공
78292 번째 증강 데이터 삽입 성공
78293 번째 증강 데이터 삽입 성공
78294 번째 증강 데이터 삽입 성공
78295 번째 증강 데이터 삽입 성공
78296 번째 증강 데이터 삽입 성공
78297 번째 증강 데이터 삽입 성공
78298 번째 증강 데이터 삽입 성공
78299 번째 증

78650 번째 증강 데이터 삽입 성공
78651 번째 증강 데이터 삽입 성공
78652 번째 증강 데이터 삽입 성공
78653 번째 증강 데이터 삽입 성공
78654 번째 증강 데이터 삽입 성공
78655 번째 증강 데이터 삽입 성공
78656 번째 증강 데이터 삽입 성공
78657 번째 증강 데이터 삽입 성공
78658 번째 증강 데이터 삽입 성공
78659 번째 증강 데이터 삽입 성공
78660 번째 증강 데이터 삽입 성공
78661 번째 증강 데이터 삽입 성공
78662 번째 증강 데이터 삽입 성공
78663 번째 증강 데이터 삽입 성공
78664 번째 증강 데이터 삽입 성공
78665 번째 증강 데이터 삽입 성공
78666 번째 증강 데이터 삽입 성공
78667 번째 증강 데이터 삽입 성공
78668 번째 증강 데이터 삽입 성공
78669 번째 증강 데이터 삽입 성공
78670 번째 증강 데이터 삽입 성공
78671 번째 증강 데이터 삽입 성공
78672 번째 증강 데이터 삽입 성공
78673 번째 증강 데이터 삽입 성공
78674 번째 증강 데이터 삽입 성공
78675 번째 증강 데이터 삽입 성공
78676 번째 증강 데이터 삽입 성공
78677 번째 증강 데이터 삽입 성공
78678 번째 증강 데이터 삽입 성공
78679 번째 증강 데이터 삽입 성공
78680 번째 증강 데이터 삽입 성공
78681 번째 증강 데이터 삽입 성공
78682 번째 증강 데이터 삽입 성공
78683 번째 증강 데이터 삽입 성공
78684 번째 증강 데이터 삽입 성공
78685 번째 증강 데이터 삽입 성공
78686 번째 증강 데이터 삽입 성공
78687 번째 증강 데이터 삽입 성공
78688 번째 증강 데이터 삽입 성공
78689 번째 증강 데이터 삽입 성공
78690 번째 증강 데이터 삽입 성공
78691 번째 증강 데이터 삽입 성공
78692 번째 증강 데이터 삽입 성공
78693 번째 증강 데이터 삽입 성공
78694 번째 증강 데이터 삽입 성공
78695 번째 증

In [21]:
len(df)

86889

In [24]:
df.tail()

idx  label class                                       conversation
86884  NaN    NaN    일반  러닝머신이나 같은 운동을 할 소리가 운동을 할 때 장의 움직임이 활발해져서 그런 거...
86885  NaN    NaN    일반  러닝머신이나 자전거 같은 운동을 할 때 소리가 게 나요.\n유산소 운동을 할 때 장...
86886  NaN    NaN    일반  러닝머신이나 때 자전거 같은 운동을 할 때 소리가 나요.\n유산소 운동을 할 때 장...
86887  NaN    NaN    일반  러닝머신이나 자전거 같은 운동을 할 때 소리가 나요.\n유산소 운동을 할 장의 움직...
86888  NaN    NaN    일반  러닝머신이나 자전거 같은 운동을 할 때 소리가 나요.\n유산소 운동을 할 때 장의 ...

In [26]:
df[df['idx'].isnull()]

idx  label class                                       conversation
7899   NaN    NaN    협박  지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 ...
7900   NaN    NaN    협박  지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 ...
7901   NaN    NaN    협박  지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 ...
7902   NaN    NaN    협박  지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 ...
7903   NaN    NaN    협박  지금 너 스스로를 죽여달라고 애원하는 것인가?\n 아닙니다. 죄송합니다.\n 죽을 ...
...    ...    ...   ...                                                ...
86884  NaN    NaN    일반  러닝머신이나 같은 운동을 할 소리가 운동을 할 때 장의 움직임이 활발해져서 그런 거...
86885  NaN    NaN    일반  러닝머신이나 자전거 같은 운동을 할 때 소리가 게 나요.\n유산소 운동을 할 때 장...
86886  NaN    NaN    일반  러닝머신이나 때 자전거 같은 운동을 할 때 소리가 나요.\n유산소 운동을 할 때 장...
86887  NaN    NaN    일반  러닝머신이나 자전거 같은 운동을 할 때 소리가 나요.\n유산소 운동을 할 장의 움직...
86888  NaN    NaN    일반  러닝머신이나 자전거 같은 운동을 할 때 소리가 나요.\n유산소 운동을 할 때 장의 ...

[78990 rows x 4 columns]